In [2]:
print('OK')

OK


In [5]:
from langchain_community.document_loaders import UnstructuredPDFLoader
from langchain_community.document_loaders import OnlinePDFLoader

In [6]:
local_path = "data/Medical_book.pdf"

# Local PDF file uploads
if local_path:
  loader = UnstructuredPDFLoader(file_path=local_path)
  data = loader.load()
else:
  print("Upload a PDF file")

In [7]:
data

[Document(page_content="TheGALEENCYCLOPEDIAofMEDICINESECONDEDITION\n\nTheGALEENCYCLOPEDIAofMEDICINESECONDEDITION\n\nVOLUMEA-B1\n\nJACQUELINE L. LONGE, EDITORDEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR\n\nSTAFFJacqueline L. Longe,Project EditorDeirdre S. Blanchfield,Associate EditorChristine B. Jeryan,Managing EditorDonna Olendorf,Senior EditorStacey Blachford,Associate EditorKate Kretschmann,Melissa C. McDade,RyanThomason,Assistant EditorsMark Springer,Technical SpecialistAndrea Lopeman,Programmer/AnalystBarbara J. Yarrow,Manager,Imaging and MultimediaContentRobyn V. Young,Project Manager,Imaging andMultimedia ContentDean Dauphinais,Senior Editor,Imaging andMultimedia ContentKelly A. Quin,Editor,Imaging and Multimedia ContentLeitha Etheridge-Sims,Mary K. Grimes,Dave Oblender,Image CatalogersPamela A. Reed,Imaging CoordinatorRandy Bassett,Imaging SupervisorRobert Duncan,Senior Imaging SpecialistDan Newell,Imaging SpecialistChristine O’Bryan,Graphic SpecialistMaria Franklin,Permissions Mana

In [8]:
# Preview first page
data[0].page_content

"TheGALEENCYCLOPEDIAofMEDICINESECONDEDITION\n\nTheGALEENCYCLOPEDIAofMEDICINESECONDEDITION\n\nVOLUMEA-B1\n\nJACQUELINE L. LONGE, EDITORDEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR\n\nSTAFFJacqueline L. Longe,Project EditorDeirdre S. Blanchfield,Associate EditorChristine B. Jeryan,Managing EditorDonna Olendorf,Senior EditorStacey Blachford,Associate EditorKate Kretschmann,Melissa C. McDade,RyanThomason,Assistant EditorsMark Springer,Technical SpecialistAndrea Lopeman,Programmer/AnalystBarbara J. Yarrow,Manager,Imaging and MultimediaContentRobyn V. Young,Project Manager,Imaging andMultimedia ContentDean Dauphinais,Senior Editor,Imaging andMultimedia ContentKelly A. Quin,Editor,Imaging and Multimedia ContentLeitha Etheridge-Sims,Mary K. Grimes,Dave Oblender,Image CatalogersPamela A. Reed,Imaging CoordinatorRandy Bassett,Imaging SupervisorRobert Duncan,Senior Imaging SpecialistDan Newell,Imaging SpecialistChristine O’Bryan,Graphic SpecialistMaria Franklin,Permissions ManagerMargaret A. Chamberl

#!ollama pull nomic-embed-text
#!ollama list
#https://github.com/tonykipkemboi/ollama_pdf_rag/blob/main/local_ollama_rag.ipynb

Vector Embedding convert text to computer read able 0 and 1

In [9]:
from langchain_community.embeddings import OllamaEmbeddings
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma

In [10]:
# Split and chunk 
text_splitter = RecursiveCharacterTextSplitter(chunk_size=7500, chunk_overlap=100)
chunks = text_splitter.split_documents(data)

In [11]:
# Add to vector database
vector_db = Chroma.from_documents(
    documents=chunks, 
    embedding=OllamaEmbeddings(model="nomic-embed-text",show_progress=True),
    collection_name="local-rag"
)

OllamaEmbeddings: 100%|██████████| 419/419 [02:59<00:00,  2.33it/s]


#Reterival

In [12]:
from langchain.prompts import ChatPromptTemplate, PromptTemplate
from langchain_core.output_parsers import StrOutputParser
from langchain_community.chat_models import ChatOllama
from langchain_core.runnables import RunnablePassthrough
from langchain.retrievers.multi_query import MultiQueryRetriever

In [18]:
# LLM from Ollama
local_model = "llama3"
llm = ChatOllama(model=local_model)

In [19]:
QUERY_PROMPT = PromptTemplate(
    input_variables=["question"],
    template="""You are an AI language model assistant. Your task is to generate five
    different versions of the given user question to retrieve relevant documents from
    a vector database. By generating multiple perspectives on the user question, your
    goal is to help the user overcome some of the limitations of the distance-based
    similarity search. Provide these alternative questions separated by newlines.
    Original question: {question}""",
)

In [20]:
retriever = MultiQueryRetriever.from_llm(
    vector_db.as_retriever(), 
    llm,
    prompt=QUERY_PROMPT
)

# RAG prompt
template = """Answer the question based ONLY on the following context:
{context}
Question: {question}
"""

prompt = ChatPromptTemplate.from_template(template)

In [21]:
chain = (
    {"context": retriever, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)

In [23]:
chain.invoke(input(""))

OllamaEmbeddings: 100%|██████████| 1/1 [00:00<00:00, 50.44it/s]


'Based on the context provided, this appears to be a medical text discussing various antiulcer drugs and their properties, side effects, and interactions. The text mentions specific medications such as Prilosec (omeprazole), Tagamet (cimetidine), Zantac (ranitidine hydrochloride), and Carafate (sucralfate), as well as conditions like gastric ulcers, gastroesophageal reflux disease (GERD), and hypersecretory syndromes.'

In [24]:
chain.invoke(input(""))

OllamaEmbeddings: 100%|██████████| 1/1 [00:00<00:00, 52.53it/s]


'Based on the provided context, the names of contributors are:\n\n1. Carol A. Turkington\n2. Jeffrey S. Dover\n\nThese individuals contributed to the medical book "Skin Deep" and possibly other sources mentioned in the document.'